# Caffe 模型

In [1]:
import sys
sys.path.extend([".."])
import set_env

ROOT: /media/pc/data/lxw/ai/tvm-book


In [2]:
from tvm_book.tools.frontends import Frontend, TrainInputConfig
from tvm_book.tools import display

caffe 前端模型配置：

In [3]:
print(display.Tree("| ")("models/caffe_demo"))

| caffe_demo
    | config.toml
    | test.caffemodel
    | test.prototxt


{icon}`fa-solid fa-folder-open` `caffe_demo/` 文件夹下存在如下内容：

- {icon}`fa-solid fa-file` `test.caffemodel` 存储 caffe 模型参数的初始化模型
- {icon}`fa-solid fa-file` `test.prototxt` 存储 caffe 模型结构
- {icon}`fa-solid fa-file` `config.toml` 存储 caffe 模型配置信息
    ```{include} models/caffe_demo/config.toml
    :code: toml
    ```

In [4]:
from pathlib import Path
import toml

cfg_path = "models/caffe_demo/config.toml"

cfg_path = Path(cfg_path)
config = toml.load(cfg_path)
frontend = Frontend(config["model"]["model_type"])
if len(config["train_inputs"]) == 1: # "此模型为单输入模型"
    input_config = TrainInputConfig(**config["train_inputs"][0])
    shape_dict = {input_config.name: input_config.shape}
    dtype_dict = {input_config.name: input_config.dtype}

model = frontend.load(
    f"{cfg_path.parent}/{config['model']['init_net_path']}", 
    predict_net_path=f"{cfg_path.parent}/{config['model']['predict_net_path']}", 
    shape_dict=shape_dict, 
    dtype_dict=dtype_dict
)

In [5]:
import tvm
from tvm import relay

with tvm.transform.PassContext(opt_level=3, disabled_pass={"AlterOpLayout"}):
    mod = relay.quantize.prerequisite_optimize(model.mod, model.params)

The Relay type checker is unable to show the following types match:
  Tensor[(1), float32]
  Tensor[(64), float32]
In particular:
  dimension 0 conflicts: 1 does not match 64.
The Relay type checker is unable to show the following types match.
In particular `Tensor[(64), float32]` does not match `Tensor[(1), float32]`
The Relay type checker is unable to show the following types match:
  Tensor[(1), float32]
  Tensor[(64), float32]
In particular:
  dimension 0 conflicts: 1 does not match 64.
The Relay type checker is unable to show the following types match.
In particular `Tensor[(64), float32]` does not match `Tensor[(1), float32]`
The Relay type checker is unable to show the following types match:
  Tensor[(1), float32]
  Tensor[(64), float32]
In particular:
  dimension 0 conflicts: 1 does not match 64.
The Relay type checker is unable to show the following types match.
In particular `Tensor[(64), float32]` does not match `Tensor[(1), float32]`
The Relay type checker is unable to show

DiagnosticError: Traceback (most recent call last):
  8: tvm::runtime::PackedFuncObj::Extractor<tvm::runtime::PackedFuncSubObj<tvm::runtime::TypedPackedFunc<tvm::IRModule (tvm::transform::Pass, tvm::IRModule)>::AssignTypedLambda<tvm::transform::__mk_TVM9::{lambda(tvm::transform::Pass, tvm::IRModule)#1}>(tvm::transform::__mk_TVM9::{lambda(tvm::transform::Pass, tvm::IRModule)#1}, std::__cxx11::basic_string<char, std::char_traits<char>, std::allocator<char> >)::{lambda(tvm::runtime::TVMArgs const&, tvm::runtime::TVMRetValue*)#1}> >::Call(tvm::runtime::PackedFuncObj const*, std::__cxx11::basic_string<char, std::char_traits<char>, std::allocator<char> >, tvm::runtime::TVMRetValue)
  7: tvm::transform::Pass::operator()(tvm::IRModule) const
  6: tvm::transform::Pass::operator()(tvm::IRModule, tvm::transform::PassContext const&) const
  5: tvm::transform::SequentialNode::operator()(tvm::IRModule, tvm::transform::PassContext const&) const
  4: tvm::transform::Pass::operator()(tvm::IRModule, tvm